In [1]:
#Python imports
import datetime
# widely used PostgreSQL connector library
import psycopg2
#pip install psycopg2
import random
from decimal import Decimal

In [2]:
from restaurant_menu import McDonald_menu, Wingstop_menu, Taco_bell_menu


In [3]:

delivery_list = ['pickup', 'delivery']

vendor_dict = { 1: McDonald_menu,
             2: Wingstop_menu,
             3: Taco_bell_menu,
    
}

country_code_iso3 = 'USA'
customer_id_list = list(range(1,10001))

RECORDS = 12001
REC_PER_DATE = 100

In [4]:
tax_list = [0,.029,.04,.04225,.0445,.045,.0475,.05,.053,.055,.056,.0575,.06,.061,.0625,.0635,.065,.06625,.0685,.06875,.07,.0725]

In [5]:
#establish the connection
conn = psycopg2.connect(
    host="localhost",
    port='5432',
    database="DE",
    user="postgres", 
    password="password")


In [6]:
#set auto commit 
conn.autocommit = True

In [7]:
#create a cursor object
cur = conn.cursor()

In [8]:
def insert(column_names, column_values, cur):
    query = f"""INSERT INTO user_purchase
    ({column_names})
    VALUES
    ({column_values});
    """

    #execute the INSERT statement
    cur.execute(query)

In [9]:
cur.execute("""SELECT table_name FROM information_schema.tables
       WHERE table_schema = 'public'""")

In [10]:
#check if table is in database
for table in cur.fetchall():
    print(table)

('user_purchase',)


In [11]:
#delete old table
query = """DELETE FROM user_purchase;
"""

In [12]:
cur.execute(query)

In [13]:
column_names="vendor_id, delivery_method, menu_items, invoice_date, tax, total, country_code_iso3, customer_id"

In [14]:
def getMenu(vendor):
    return vendor_dict[vendor]
        

In [15]:
#Get the total from the dictionary values
#Since we need precision use Decimal
def getDictTotal(item_dict):
    values_list = item_dict.values()
    total = Decimal(0)
    for value in values_list:
        num = Decimal(value)
        total += num
    return total

In [16]:
def checkKey(item_dict, key):
    #check if empty
    #empty dictionary are false 
    if (bool(item_dict) == False):
        return False
    elif key in item_dict.keys():
        return True
    else:
        return False

In [17]:
def addItem(item_dict, menu):
    rnum = random.randrange(0,len(menu))
    print(f"item_dict = {item_dict}")
    print(f"random item = {rnum}")
    key = list(menu)[rnum]
    print(f"key = {key}")
    val = list(menu.values())[rnum]
    print(f"val = {val}")
    temp = {key: val}
    #check if key already in item_dict
    isDuplicate = checkKey(item_dict, key)
    
   # try:
        #if duplicate  
    if(isDuplicate):
        x = item_dict[key]
        
        #check if x is zero
        #if it's zero do nothing
        #add a way to count zero items later
        if(x!=0):
        
            #check number of duplicates
            count = val/x
            #round to nearest integer 
            count = round(count)
            print(f"count = {count}")
            
            #example new burger is now
            # (1) Double Burger
            key = f"({count}) {key}"
            print(f"new key = {key}")
            temp = {key:val}
            print("it is duplicate")
            print(f"item_dict = {item_dict}")
            item_dict[key] = val
            print(f"item_dict = {item_dict}")
    #not duplicate add new key-value pair
    else:
        print(f"key = {key}")
        print(f"val = {val}")
        print(f"item_dict = {item_dict}")
        item_dict[key]=val

    #except (Exception) as error:
    #    print(error)
        
    
    return item_dict

In [18]:
def getItemList(menu, rnum, item_dict ):
    print("------------------")
    print(f"rnum = {rnum}")
    item_dict = item_dict
    if(rnum > 0):
        item_dict = addItem(item_dict, menu)
        getItemList(menu, rnum-1, item_dict)
    return item_dict

In [19]:
def print_date(date_obj):
    date_format="%Y-%m-%d"
    print(date_obj.strftime(date_format))


In [20]:
def increment_date(date_obj):
    date_obj += datetime.timedelta(days=1)
    return date_obj

In [21]:
def create_date_obj(year, month, day):
    date_obj = datetime.datetime(year, month, day)
    return date_obj

In [22]:
def get_col_2(start, end):
    rnum = random.randrange(start, end)
    return rnum

In [23]:
def get_col_3(start, end):
    rnum = random.randrange(0,2)
    delivery_method = delivery_list[rnum]
    return delivery_method

In [24]:
#get number of items ordered from 1 - end
def get_items_ordered(start, end):
    rnum = random.randrange(start, end)
    return rnum

In [25]:
def get_csv_from_dict(dictionary):
    new_list = list(dictionary)
    new_csv = '|'.join(new_list)
    return new_csv

In [26]:
def get_customer_id(rnum):
    customer_id = customer_id_list[rnum]
    return customer_id

In [27]:
def get_col_9(start, end):
    rnum= random.randrange(start,end)
    customer_id = get_customer_id(rnum)
    return customer_id

In [28]:
def get_item_dict(vendor_id, start,end):
    
    items_ordered = get_items_ordered(start, end)
    menu_dict = getMenu(vendor_id) #get menu dictionary

    item_dict={}
    item_dict = getItemList(menu_dict,items_ordered, item_dict)
    
    return item_dict


In [29]:
def get_col_6():
    rnum = random.randrange(0, len(tax_list))
    tax = tax_list[rnum]
    return tax

In [30]:
def get_col_7(item_dict, tax):
    item_total = getDictTotal(item_dict)
    item_total = round(item_total, 2)

    #convert to decimal
    tax = Decimal(tax)
    item_tax =  item_total* tax
    #round number to closest two decimal places
    item_tax = round(item_tax,2)

    total = item_total + item_tax
    return total

In [31]:

    

date_obj = create_date_obj(2023,1,1)

for i in range(1,RECORDS):
    
    if((i%REC_PER_DATE) == 0):
        date_obj = increment_date(date_obj)

    vendor_id = get_col_2(1,4)
    col_2=vendor_id
    
    delivery_method = get_col_3(0,2)
    col_3=delivery_method
        
    
    item_dict = get_item_dict(vendor_id, 1,4)
    item_csv = get_csv_from_dict(item_dict)
    col_4=item_csv
    
    col_5=date_obj

    tax = get_col_6()
    col_6= tax
    
    
    total =get_col_7(item_dict, tax)
    col_7=total
    
    col_8=country_code_iso3

    customer_id = get_col_9(0, 10000)
    col_9= customer_id
    
    column_values = f" {col_2} , '{col_3}' , '{col_4}' ,'{col_5}' ,{col_6} ,{col_7} ,'{col_8}', {col_9}"

    
    insert(column_names, column_values, cur)


------------------
rnum = 1
item_dict = {}
random item = 34
key = 3 Doritos Locos Tacos Combo
val = 8.89
key = 3 Doritos Locos Tacos Combo
val = 8.89
item_dict = {}
------------------
rnum = 0
------------------
rnum = 2
item_dict = {}
random item = 124
key = Chips And Nacho Cheese Sauce
val = 1.69
key = Chips And Nacho Cheese Sauce
val = 1.69
item_dict = {}
------------------
rnum = 1
item_dict = {'Chips And Nacho Cheese Sauce': 1.69}
random item = 69
key = Pintos N Cheese
val = 2.19
key = Pintos N Cheese
val = 2.19
item_dict = {'Chips And Nacho Cheese Sauce': 1.69}
------------------
rnum = 0
------------------
rnum = 2
item_dict = {}
random item = 10
key = 15pc Meal for 2 Mix & Match
val = 25.09
key = 15pc Meal for 2 Mix & Match
val = 25.09
item_dict = {}
------------------
rnum = 1
item_dict = {'15pc Meal for 2 Mix & Match': 25.09}
random item = 11
key = 15pc Meal for 2 Classic
val = 25.09
key = 15pc Meal for 2 Classic
val = 25.09
item_dict = {'15pc Meal for 2 Mix & Match': 25.09}


------------------
rnum = 1
item_dict = {}
random item = 151
key = Medium Strawberry Shake
val = 3.69
key = Medium Strawberry Shake
val = 3.69
item_dict = {}
------------------
rnum = 0
------------------
rnum = 1
item_dict = {}
random item = 20
key = 40pc Group Pack Classic
val = 52.89
key = 40pc Group Pack Classic
val = 52.89
item_dict = {}
------------------
rnum = 0
------------------
rnum = 3
item_dict = {}
random item = 35
key = 3 Doritos Locos Tacos Supreme Combo
val = 10.19
key = 3 Doritos Locos Tacos Supreme Combo
val = 10.19
item_dict = {}
------------------
rnum = 2
item_dict = {'3 Doritos Locos Tacos Supreme Combo': 10.19}
random item = 27
key = Mexican Pizza Combo
val = 9.89
key = Mexican Pizza Combo
val = 9.89
item_dict = {'3 Doritos Locos Tacos Supreme Combo': 10.19}
------------------
rnum = 1
item_dict = {'3 Doritos Locos Tacos Supreme Combo': 10.19, 'Mexican Pizza Combo': 9.89}
random item = 59
key = Crunchwrap Supreme
val = 5.29
key = Crunchwrap Supreme
val = 5.29
it

------------------
rnum = 2
item_dict = {}
random item = 127
key = Equal Packet
val = 0.0
key = Equal Packet
val = 0.0
item_dict = {}
------------------
rnum = 1
item_dict = {'Equal Packet': 0.0}
random item = 139
key = Spicy Buffalo
val = 0.0
key = Spicy Buffalo
val = 0.0
item_dict = {'Equal Packet': 0.0}
------------------
rnum = 0
------------------
rnum = 3
item_dict = {}
random item = 36
key = 3 Soft Tacos Combo
val = 7.39
key = 3 Soft Tacos Combo
val = 7.39
item_dict = {}
------------------
rnum = 2
item_dict = {'3 Soft Tacos Combo': 7.39}
random item = 13
key = Breakfast Crunchwrap Sausage
val = 3.29
key = Breakfast Crunchwrap Sausage
val = 3.29
item_dict = {'3 Soft Tacos Combo': 7.39}
------------------
rnum = 1
item_dict = {'3 Soft Tacos Combo': 7.39, 'Breakfast Crunchwrap Sausage': 3.29}
random item = 109
key = Cup Of Water
val = 0.0
key = Cup Of Water
val = 0.0
item_dict = {'3 Soft Tacos Combo': 7.39, 'Breakfast Crunchwrap Sausage': 3.29}
------------------
rnum = 0
--------

------------------
rnum = 1
item_dict = {}
random item = 103
key = Medium Latte
val = 3.29
key = Medium Latte
val = 3.29
item_dict = {}
------------------
rnum = 0
------------------
rnum = 3
item_dict = {}
random item = 73
key = Fire Sauce Packet
val = 0.0
key = Fire Sauce Packet
val = 0.0
item_dict = {}
------------------
rnum = 2
item_dict = {'Fire Sauce Packet': 0.0}
random item = 66
key = Chips and Nacho Cheese Sauce
val = 2.19
key = Chips and Nacho Cheese Sauce
val = 2.19
item_dict = {'Fire Sauce Packet': 0.0}
------------------
rnum = 1
item_dict = {'Fire Sauce Packet': 0.0, 'Chips and Nacho Cheese Sauce': 2.19}
random item = 49
key = Beefy 5-Layer Burrito
val = 3.99
key = Beefy 5-Layer Burrito
val = 3.99
item_dict = {'Fire Sauce Packet': 0.0, 'Chips and Nacho Cheese Sauce': 2.19}
------------------
rnum = 0
------------------
rnum = 2
item_dict = {}
random item = 42
key = Bacon Egg Cheese McGriddle
val = 4.99
key = Bacon Egg Cheese McGriddle
val = 4.99
item_dict = {}
----------

------------------
rnum = 1
item_dict = {}
random item = 24
key = Crunchwrap Supreme Cravings Trio
val = 5.0
key = Crunchwrap Supreme Cravings Trio
val = 5.0
item_dict = {}
------------------
rnum = 0
------------------
rnum = 3
item_dict = {}
random item = 172
key = Medium Frozen Fanta (Wild Cherry)
val = 2.09
key = Medium Frozen Fanta (Wild Cherry)
val = 2.09
item_dict = {}
------------------
rnum = 2
item_dict = {'Medium Frozen Fanta (Wild Cherry)': 2.09}
random item = 71
key = Quarter Pounder With Cheese Deluxe Meal
val = 8.79
key = Quarter Pounder With Cheese Deluxe Meal
val = 8.79
item_dict = {'Medium Frozen Fanta (Wild Cherry)': 2.09}
------------------
rnum = 1
item_dict = {'Medium Frozen Fanta (Wild Cherry)': 2.09, 'Quarter Pounder With Cheese Deluxe Meal': 8.79}
random item = 115
key = Medium Americano
val = 2.79
key = Medium Americano
val = 2.79
item_dict = {'Medium Frozen Fanta (Wild Cherry)': 2.09, 'Quarter Pounder With Cheese Deluxe Meal': 8.79}
------------------
rnum = 

...

------------------
rnum = 1
item_dict = {}
random item = 10
key = 15pc Meal for 2 Mix & Match
val = 25.09
key = 15pc Meal for 2 Mix & Match
val = 25.09
item_dict = {}
------------------
rnum = 0
------------------
rnum = 2
item_dict = {}
random item = 77
key = Creamy Jalapeno Sauce
val = 0.1
key = Creamy Jalapeno Sauce
val = 0.1
item_dict = {}
------------------
rnum = 1
item_dict = {'Creamy Jalapeno Sauce': 0.1}
random item = 7
key = Grande Toasted Breakfast Burrito Combo
val = 5.69
key = Grande Toasted Breakfast Burrito Combo
val = 5.69
item_dict = {'Creamy Jalapeno Sauce': 0.1}
------------------
rnum = 0
------------------
rnum = 1
item_dict = {}
random item = 42
key = 50 Wings Boneless
val = 50.39
key = 50 Wings Boneless
val = 50.39
item_dict = {}
------------------
rnum = 0
------------------
rnum = 3
item_dict = {}
random item = 38
key = Burrito Supreme Combo
val = 9.59
key = Burrito Supreme Combo
val = 9.59
item_dict = {}
------------------
rnum = 2
item_dict = {'Burrito Suprem

------------------
rnum = 1
item_dict = {}
random item = 141
key = Butter
val = 0.0
key = Butter
val = 0.0
item_dict = {}
------------------
rnum = 0
------------------
rnum = 1
item_dict = {}
random item = 16
key = 30pc Crew Pack Mix & Match
val = 41.39
key = 30pc Crew Pack Mix & Match
val = 41.39
item_dict = {}
------------------
rnum = 0
------------------
rnum = 2
item_dict = {}
random item = 16
key = Cinnabon Delights 12 Pack
val = 6.69
key = Cinnabon Delights 12 Pack
val = 6.69
item_dict = {}
------------------
rnum = 1
item_dict = {'Cinnabon Delights 12 Pack': 6.69}
random item = 113
key = Chips And Nachos Cheese Sauce
val = 2.19
key = Chips And Nachos Cheese Sauce
val = 2.19
item_dict = {'Cinnabon Delights 12 Pack': 6.69}
------------------
rnum = 0
------------------
rnum = 3
item_dict = {}
random item = 112
key = Nachos BellGrande
val = 6.49
key = Nachos BellGrande
val = 6.49
item_dict = {}
------------------
rnum = 2
item_dict = {'Nachos BellGrande': 6.49}
random item = 114


------------------
rnum = 3
item_dict = {}
random item = 34
key = 15 Wings Mix & Match
val = 17.49
key = 15 Wings Mix & Match
val = 17.49
item_dict = {}
------------------
rnum = 2
item_dict = {'15 Wings Mix & Match': 17.49}
random item = 65
key = Louisiana Voodoo Fries Regular
val = 4.59
key = Louisiana Voodoo Fries Regular
val = 4.59
item_dict = {'15 Wings Mix & Match': 17.49}
------------------
rnum = 1
item_dict = {'15 Wings Mix & Match': 17.49, 'Louisiana Voodoo Fries Regular': 4.59}
random item = 74
key = Iced Tea 20oz
val = 2.69
key = Iced Tea 20oz
val = 2.69
item_dict = {'15 Wings Mix & Match': 17.49, 'Louisiana Voodoo Fries Regular': 4.59}
------------------
rnum = 0
------------------
rnum = 2
item_dict = {}
random item = 164
key = Medium Root Beer
val = 1.79
key = Medium Root Beer
val = 1.79
item_dict = {}
------------------
rnum = 1
item_dict = {'Medium Root Beer': 1.79}
random item = 112
key = Medium Vanilla Cappuccino
val = 3.29
key = Medium Vanilla Cappuccino
val = 3.29


------------------
rnum = 1
item_dict = {}
random item = 104
key = Medium Caramel Latte
val = 3.29
key = Medium Caramel Latte
val = 3.29
item_dict = {}
------------------
rnum = 0
------------------
rnum = 3
item_dict = {}
random item = 153
key = Oreo Fudge McFlurry
val = 4.29
key = Oreo Fudge McFlurry
val = 4.29
item_dict = {}
------------------
rnum = 2
item_dict = {'Oreo Fudge McFlurry': 4.29}
random item = 140
key = Syrup
val = 0.2
key = Syrup
val = 0.2
item_dict = {'Oreo Fudge McFlurry': 4.29}
------------------
rnum = 1
item_dict = {'Oreo Fudge McFlurry': 4.29, 'Syrup': 0.2}
random item = 158
key = Medium Hi-C Orange
val = 1.79
key = Medium Hi-C Orange
val = 1.79
item_dict = {'Oreo Fudge McFlurry': 4.29, 'Syrup': 0.2}
------------------
rnum = 0
------------------
rnum = 2
item_dict = {}
random item = 185
key = Cheeseburger
val = 2.09
key = Cheeseburger
val = 2.09
item_dict = {}
------------------
rnum = 1
item_dict = {'Cheeseburger': 2.09}
random item = 4
key = Sausage Egg Chees

------------------
rnum = 2
item_dict = {}
random item = 165
key = Medium Minute Maid Orange Juice
val = 3.29
key = Medium Minute Maid Orange Juice
val = 3.29
item_dict = {}
------------------
rnum = 1
item_dict = {'Medium Minute Maid Orange Juice': 3.29}
random item = 52
key = Bagel
val = 1.69
key = Bagel
val = 1.69
item_dict = {'Medium Minute Maid Orange Juice': 3.29}
------------------
rnum = 0
------------------
rnum = 1
item_dict = {}
random item = 45
key = 75 Wings Boneless
val = 74.49
key = 75 Wings Boneless
val = 74.49
item_dict = {}
------------------
rnum = 0
------------------
rnum = 1
item_dict = {}
random item = 40
key = Sausage McMuffin
val = 2.19
key = Sausage McMuffin
val = 2.19
item_dict = {}
------------------
rnum = 0
------------------
rnum = 2
item_dict = {}
random item = 13
key = 24pc Family Pack Mix & Match
val = 34.49
key = 24pc Family Pack Mix & Match
val = 34.49
item_dict = {}
------------------
rnum = 1
item_dict = {'24pc Family Pack Mix & Match': 34.49}
rand

In [32]:
column_values = f" {col_2} , '{col_3}' , '{col_4}' ,'{col_5}' ,{col_6} ,{col_7} ,'{col_8}', {col_9}"

print(column_values)

 2 , 'delivery' , '50 Wings Mix & Match|Iced Tea 32oz' ,'2023-05-01 00:00:00' ,0.065 ,64.73 ,'USA', 8343


In [33]:
def get_last_row(cur):
    #get last row of user_purchase
    query = """SELECT * FROM user_purchase
    WHERE invoice_number=(SELECT max(invoice_number) FROM user_purchase);
    """
    cur.execute(query)
    result = cur.fetchone()
    return result

In [34]:
result = get_last_row(cur)
print(result[0])

55102


In [35]:
def get_all_records(cur):
    query = """SELECT * FROM user_purchase;"""
    cur.execute(query)
    result = cur.fetchall()
    return result

In [36]:
print(get_all_records(cur))

[(43103, 3, 'pickup', '3 Doritos Locos Tacos Combo', datetime.date(2023, 1, 1), Decimal('0.04500'), Decimal('9.29'), 'USA', 7779), (43104, 3, 'pickup', 'Chips And Nacho Cheese Sauce|Pintos N Cheese', datetime.date(2023, 1, 1), Decimal('0.07000'), Decimal('4.15'), 'USA', 1401), (43105, 2, 'delivery', '15pc Meal for 2 Mix & Match|15pc Meal for 2 Classic', datetime.date(2023, 1, 1), Decimal('0.05500'), Decimal('52.94'), 'USA', 5081), (43106, 1, 'pickup', 'Double Smoky BLT Quarter Pounder With Cheese|Scrambled Eggs|Medium Caramel Mocha', datetime.date(2023, 1, 1), Decimal('0.07000'), Decimal('15.59'), 'USA', 2245), (43107, 2, 'delivery', 'Veggie Sticks Carrots Only|Large 10 pc Wing Combo Boneless|Iced Tea 20oz', datetime.date(2023, 1, 1), Decimal('0.02900'), Decimal('17.26'), 'USA', 2360), (43108, 3, 'pickup', 'Grande Toasted Breakfast Burrito Combo|Black Beans And Rice', datetime.date(2023, 1, 1), Decimal('0.06000'), Decimal('7.93'), 'USA', 818), (43109, 1, 'delivery', 'Medium Root Beer|B

In [39]:
def get_tbl_count(cur):
    query = """SELECT COUNT(*) FROM user_purchase """
    cur.execute(query)
    result = cur.fetchone()
    print(result)

In [40]:
get_tbl_count(cur)

(12000,)


In [ ]:
#Closing the connection
conn.close()